# Quantization of real numbers

In [1]:
Aq.<q> = PolynomialRing(ZZ)
Zq = Frac(Aq)

## Integers

In [6]:
def qint(n):
    return (q^n-1)/(q-1)

def qfactorial(n):
    p = 1
    for i in range(1,n+1):
        p = p*qint(i)
    return p

def qbinom(k,n):
    return qfactorial(n)/(qfactorial(k)*qfactorial(n-k))

In [7]:
qbinom(2,4)

q^4 + q^3 + 2*q^2 + q + 1

## Rational numbers

In [8]:
R = matrix(Zq,[[q,1],[0,1]])
L = matrix(Zq,[[q,0],[q,1]])
N = Matrix(Zq,[[-1,1-q^(-1)],[q-1,1]])
S = -q^(-1)*R*L^(-1)*R
J = q*N*S

In [11]:
print(R)
print(" ")
print(J)

[q 1]
[0 1]
 
[ q - 1      1]
[     q -q + 1]


In [15]:
# Decomposition in continued fractions

# fraction_plus : 
# input = a rational number x
# output = the positive continued fraction of x with an even number of terms

def fraction_plus(x):
    a = list(x.continued_fraction())
    n = len(a)
    if n%2 == 1:
        a[n-1] = a[n-1] - 1
        a.append(1) 
    return a

# fraction_moins : 
# input = a rational number x
# output = the negative continued fraction of x

def fraction_moins(x):
    a = fraction_plus(x)
    n = len(a)
    c = [a[0]+1]
    for j in range(a[1]-1):
        c.append(2)
    for i in range(1,n//2):
        c.append(a[2*i]+2)
        for j in range(a[2*i+1]-1):
            c.append(2)
    return c

In [13]:
fraction_plus(5/2)

[2, 2]

In [14]:
fraction_moins(5/2)

[3, 2]

In [17]:
# Computation of continued fractions

# calculer_plus : 
# input = a list of integers a
# output = a rational number, result of the positive continued fraction given by the list a

def calculer_plus(a):
    if len(a)==1:
        return a[0]
    else:
        return a[0] + 1/calculer_plus(a[1:])
    
# calculer_moins : 
# input = a list of integers c
# output = a rational number, result of the negative continued fraction given by the list c

def calculer_moins(c):
    if len(c)==1:
        return c[0]
    else:
        return c[0] - 1/calculer_moins(c[1:])

In [18]:
calculer_plus([2,2])

5/2

In [20]:
calculer_moins([3,2])

5/2

In [21]:
# q-deformed matrices

# qMplus :
# input = a list of integers a
# output = the positive quantized matrix defined by this list 

def qMplus(a):
    n = len(a)
    if n%2 == 1:
        return "n doit etre pair"
    Mplus = matrix(Zq,[[1,0],[0,1]])
    for i in range(n):
        if i%2 == 0:
            Mplus = Mplus*R^(a[i])
        else:
            Mplus = Mplus*L^(a[i])
    return Mplus

# qMmoins :
# input = a list of integers ci
# output = the negative quantized matrix defined by this list 

def qMmoins(ci):
    Mmoins = matrix(Zq,[[1,0],[0,1]])
    for y in ci:
        Mmoins = Mmoins*(R^y)*S
    return Mmoins

# matrix_specialized :
# input = a matrix whose coefficients are Laurent polynomials in q
# output = the same matrix when q=1 

def matrix_specialized(M):
    a = ZZ(M[0,0](1))
    b = M[0,1](1)
    c = M[1,0](1)
    d = M[1,1](1)
    M_1 = matrix(ZZ,[[a,b],[c,d]])
    return M_1

# qMplusJ :
# input = a list of integers a
# output = the odd positive quantized matrix given by the list a

def qMplusJ(a):
    n = len(a)
    Mplus_odd = matrix(Zq,[[1,0],[0,1]])
    for i in range(n):
        Mplus_odd = Mplus_odd*R^(a[i])*J
    return Mplus_odd

In [27]:
M = qMplus([2,2])
print(M)
print(" ")
print(qMmoins([3,2]))
print(" ")
print(matrix_specialized(M))
print(" ")
print(qMplusJ([2,1,1]))

[q^4 + q^3 + 2*q^2 + q                 q + 1]
[              q^2 + q                     1]
 
[q^3 + q^2 + 2*q + 1      -q^3 - q^2 - q]
[              q + 1                  -q]
 
[5 2]
[2 1]
 
[  q^7 + q^5 + q^4 + q^3 + q       q^5 - q^4 + 2*q^3 + 1]
[q^5 - q^4 + 2*q^3 - q^2 + q                 q^2 - q + 1]


In [28]:
# Quantized rational numbers, right and left versions

def qrationnel(x):
    a = fraction_plus(x)
    M = qMplus(a)
    V = M*vector(Zq,[[1],[0]])
    return V[0]/V[1]

def left_qrationnel(x):
    a = fraction_plus(x)
    M = qMplus(a)
    V = M*vector(Zq,[[1],[1-q]])
    return V[0]/V[1]

In [29]:
x = 29/17
print(qrationnel(x))
print(" ")
print(left_qrationnel(x))

(q^7 + 3*q^6 + 5*q^5 + 6*q^4 + 6*q^3 + 5*q^2 + 2*q + 1)/(q^6 + 2*q^5 + 3*q^4 + 4*q^3 + 4*q^2 + 2*q + 1)
 
(q^8 + 2*q^7 + 4*q^6 + 5*q^5 + 5*q^4 + 5*q^3 + 4*q^2 + 2*q + 1)/(q^7 + q^6 + 3*q^5 + 3*q^4 + 3*q^3 + 3*q^2 + 2*q + 1)


## Irrational numbers

In [30]:
# New formal variables for the formal Laurent series
var('y')

y

In [34]:
# Quantized real number

# qreel :
# input = a real number 'x' and a positive integer 'borne'
# output = the first terms of the series defining the quantization of x, 
# computed from the first 'borne' terms of the positive continued fraction of x.

def qreel(x,borne):
    sequence = list(continued_fraction(x)[:borne])
    d = sum(sequence) - 2
    x_n = calculer_plus(sequence)
    qx_n = (qrationnel(x_n)(y)).taylor(y,0,d)
    return qx_n

In [35]:
x = RR((1+sqrt(5))/2)
qreel(x,12)

185*y^10 - 82*y^9 + 37*y^8 - 17*y^7 + 8*y^6 - 4*y^5 + 2*y^4 - y^3 + y^2 + 1

In [37]:
x = math.pi
qreel(x,4)

4*y^24 + 2*y^23 - y^22 - 2*y^21 - y^20 + y^16 + y^15 - y^13 - y^12 + y^10 + y^2 + y + 1

## Quadratic irrational numbers

In [38]:
# Solving Pell-Fermat equation
# input = an positive integer delta 
# output = two integers num,denom satisfying num^2 - delta*denom^2 = 1

def solve_Fermat(delta):
    sequence = list(continued_fraction(sqrt(delta))[:50])
    i = 1
    b = False
    while not b:
        xi = calculer_plus(sequence[:i])
        num = xi.numerator()
        denom = xi.denominator()
        b = (num^2 - denom^2*delta == 1)
        i+=1
    return (num,denom)

In [40]:
(a,b) = solve_Fermat(20)
print((a,b))
print(a^2 - 20*b^2)

(9, 2)
1


In [42]:
# Computing a matrix M fixing x
# input = a quadratic irrational number x
# output = a matrix M in SL_2(ZZ) such that x is a fixed point of M

def fixing_matrix(x):
    pi = x.minpoly()
    if pi.degree() != 2:
        print("x doit etre irrationnel quadratique")
    else:
        delta = pi[1]^2 - 4*pi[0]*pi[2]
        (mu_prime,lambda_prime) = solve_Fermat(delta)
        a = -lambda_prime*pi[1] + mu_prime
        b = -2*lambda_prime*pi[0]
        c = 2*lambda_prime*pi[2]
        d = 2*lambda_prime*pi[1] +a
        M = matrix(ZZ,[[a,b],[c,d]])
        return M

In [45]:
x = (1+sqrt(5))/2
print(RR(x))
print(" ")
M = fixing_matrix(x)
print(M)
print(" ")
w = M*vector(RR,[x,1])
print(RR(w[0]/w[1]))

1.61803398874989
 
[13  8]
[ 8  5]
 
1.61803398874989


In [46]:
# Decomposing a matrix M on the generators R and S
# input = a matrix M of SL_2(ZZ)
# output = a list of integers c = [c1,c2,...,ck] such that R^(c1)*S*R^(c2)*S*...*R^(ck)*S = M in PSL2(ZZ).

def decompose(M):
    a = M[0,0]
    b = M[0,1]
    c = M[1,0]
    d = M[1,1]
    if c == 0:
        coeffs = []
    else:
        coeffs = fraction_moins(a/c)
    R_e = (matrix_specialized(qMmoins(coeffs))^(-1))*M
    k = R_e[0,1]
    if k > 0:
        return [y for y in coeffs] + [k+1,1,1]
    elif k == 0:
        return [y for y in coeffs]
    else:
        return [y for y in coeffs[:-1]] + [coeffs[-1]+1] + [2 for i in range(-k-1)] + [1]
    

In [50]:
M = matrix(ZZ,[[13,8],[8,5]])
ci = decompose(M)
print(ci)
print(" ")
print(matrix_specialized(qMmoins(ci)))

[2, 3, 3, 2, 1, 1]
 
[-13  -8]
[ -8  -5]


In [51]:
# Quantized quadratic irrational number

# sol_radicaux :
# input = a quadratic irrational number x
# output = the three polynomials B,P,A, such that [x]_q = (B+sqrt(P))/A

def sol_radicaux(x):
    M = fixing_matrix(x)
    #print(M)
    ci = decompose(M)
    #print(ci)
    Mq = qMmoins(ci)
    s = 0
    for c in ci:
        s += c-1
    P = Aq(Mq.trace()^2 - 4*q^s)
    B = Aq(Mq[0,0] - Mq[1,1])
    A = Aq(2*Mq[1,0])
    # Simplifier des facteurs potentiels
    facteur = gcd(B,A)
    facteur = gcd(facteur,P)
    if P%(facteur^2) == 0:
        B = B//facteur
        A = A//facteur
        P = P//(facteur)^2
    return (B,P,A)


# q_quadratic_equation :
# input = a quadratic irrational number x
# output = no output, but print of the minimal polynomial of x and of the quantized minimal polynomial of x

def q_quadratic_equation(x):
    M = fixing_matrix(x)
    ci = decompose(M)
    Mq = qMmoins(ci)
    A = Mq[0,0]
    B = Mq[0,1]
    C = Mq[1,0]
    D = Mq[1,1]
    facteur = gcd(C,B)
    facteur = gcd(facteur,D-A)
    C = C//facteur
    B = B//facteur
    E = (D-A)//facteur
    print("classical equation :",x.minpoly())
    print(" ")
    print("quantized equation :")
    print('('+str(C)+')x^2 + ('+str(E)+')x + ('+str(-B)+')')

In [53]:
x = (1+sqrt(5))/2

print(sol_radicaux(x))
print(" ")
q_quadratic_equation(x)

(-q^2 - q + 1, q^4 + 2*q^3 - q^2 + 2*q + 1, -2*q)
 
classical equation : x^2 - x - 1
 
quantized equation :
(-q)x^2 + (q^2 + q - 1)x + (1)
